In [116]:
import pandas as pd
import numpy as np
import math
import requests
from yelpapi import YelpAPI
from pandas.io.json import json_normalize
import pandas_profiling

Info about the Yelp API
Parameters:
* limit = Number of business results to return. By default, it will return 20. Maximum is 50.
* offset = Offset the list of returned business results by this amount. For example if there are 300 businesses, in the first requests there's a max of 50 restaurants sent back to us, in the second we'll do offset = 50 which will get us the businesses from 50 to 100. These still are considered as different requests


* Client ID

B8rRuDSzKbPnW3jBOwXdZg

**API Keys**

* irBVcEgoI6PeOStlUs77hlL-9r0MA5oa14yFIdtA_mtpe3ChIaN8rAyLcCGgQAFQdfI4cK2ZY84cx3ZFIMh2bDBgIotdi_9yN3Xlp23eE-9HF-Ou5vTrErRnngbIXXYx

* gWozwadRpB03ay6xxc0rrs4w5Qy5rzB59xQDaaKjcAeXmtZ6D_R8fNQCClj-rga4CgtDRMDqgYVkYn5KvXMn3MYXf5VKSttOE21qbxoCHebmOMb5k_9GFykHvVLZXXYx




To get these, must visit https://www.yelp.com/developers/v3/manage_app and create an account

In [259]:
API_KEY = 'gWozwadRpB03ay6xxc0rrs4w5Qy5rzB59xQDaaKjcAeXmtZ6D_R8fNQCClj-rga4CgtDRMDqgYVkYn5KvXMn3MYXf5VKSttOE21qbxoCHebmOMb5k_9GFykHvVLZXXYx'
#Endpoints : https://www.yelp.com/developers/documentation/v3

MAX_RETURNS = 50
HEADERS = {'Authorization': 'bearer %s' % API_KEY}

## BUSINESS SEARCH ENDPOINT: Make general requests about Chicago

In [3]:
ENDPOINT = 'https://api.yelp.com/v3/businesses/search'

In [4]:
#Define the inital parameters
INIT_PARAM = {'offset': 0,
             'limit' : 1,
              'term' : 'food',
             'location':'Chicago'}

In [ ]:
# find out how many establishment we can collect 
init_response = requests.get(url=ENDPOINT, params=INIT_PARAM, headers = HEADERS)
nb_estab = response.json()['total']
print('The number of establishments satifying the request is : {0} establishments'.format(nb_estab))

# The YelpAPI only returns 50 establishments at a time, and returns in total up to 1000 items
# the number of requests we'll have to make is ceil(the number of establishments divided by 50)
nb_requests = math.ceil(nb_estab / MAX_RETURNS) if (nb_estab < 1000) else 20
print('We will have to make {0} requests'.format(nb_requests))

In [ ]:
#create dataframe to contain businesses
businesses = pd.DataFrame()

#Make requests and fill up the dataframe
for req in range(nb_requests):
    # the offset is the starting points in Yelp database
    PARAM = {'offset': req*50,
             'limit' : 50,
              'term' : 'food',
             'location':'Chicago'}
    response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
    businesses = businesses.append(json_normalize(response.json()['businesses']), ignore_index=True)

#### Clean data

In [ ]:
#drop useless columns
businesses = businesses.drop(columns=['image_url', 'transactions', 'url','location.address1', 'location.address2',\
                         'location.address3', 'phone','location.display_address', 'display_phone',\
                         'distance'])

In [ ]:
#Only keep establishments in Illinois
businesses = businesses[businesses['location.state'] == 'IL']

In [ ]:
print(businesses['location.city'].unique())

#after checking out these locations individually, we find that they are close to Chicago, so we can keep them

In [ ]:
businesses.to_pickle("yelp_businesses_pickle")

## BUSINESS SEARCH ENDPOINT: Make requests about establishment from the Chicago food inspections dataset

In [ ]:
ENDPOINT = 'https://api.yelp.com/v3/businesses/search'

<font color='red'>
How are we going to automatize the process of choosing the best yelp response ?  => Join ?

<font color='red'>
Yelp is stupid: if we send request CARNICERIA Y FRUTERIA 'LOS ALTOS' INC it's won't recognize it, but if we send the same without the INC, it does

## BUSINESS MATCH ENDPOINT: Make requests about establishment from the Chicago food inspections dataset

In [59]:
ENDPOINT = 'https://api.yelp.com/v3/businesses/matches'

### Tests (test here for an individual establishment)

In [244]:
#Define the parameters
PARAM = {'name': 'LA CATRINA RESTAURANT LLC', 'address1': '3924 W DIVERSEY AVE ', 'city': 'Chicago', 'state': 'IL', 'country': 'US'}

In [245]:
response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)

In [246]:
#json_normalize(response.json()['businesses'])

In [247]:
response.headers

{'Server': 'nginx', 'Content-Type': 'application/json', 'x-routing-service': '10-65-208-15-useast1cprod; site=public_api_v3', 'x-b3-sampled': '0', 'x-zipkin-id': 'a463066aa41e7b6b', 'ratelimit-remaining': '0', 'ratelimit-resettime': '2019-11-24T00:00:00+00:00', 'ratelimit-dailylimit': '5000', 'x-proxied': '10-65-214-75-useast1cprod', 'Content-Length': '230', 'Accept-Ranges': 'bytes', 'Date': 'Sat, 23 Nov 2019 15:29:13 GMT', 'Via': '1.1 varnish', 'Connection': 'keep-alive', 'X-Served-By': 'cache-hhn4023-HHN', 'X-Cache': 'MISS', 'X-Cache-Hits': '0'}

### Reading the (non clean) dataset

In [215]:
estab = pd.read_pickle("insp_businesses_pickle")

In [216]:
estab.head(5)

DBA Name                         AKA Name  \
0                  YOUNG SCHOLARS ACADEMY           YOUNG SCHOLARS ACADEMY   
1                             OSITO'S TAP                      OSITO'S TAP   
2                        LAS SISTERS INC.                  LAS SISTERS INC   
3  CARNICERIA Y FRUTERIA 'LOS ALTOS' INC.  CARNICERIA Y FRUTERIA LOS ALTOS   
4                  FOODA- 150 N RIVERSIDE            FOODA 150 N RIVERSIDE   

                      Address                           Facility Type  
0  10926-10928 S WESTERN AVE                    Daycare (2 - 6 Years)  
1        2553 S RIDGEWAY AVE                               Restaurant  
2        2700 S TRUMBULL AVE                               Restaurant  
3             2959 W 40TH ST                            Grocery Store  
4        150 N RIVERSIDE PLZ   Pop-Up Food Establishment User-Tier II

In [217]:
estab = estab[['DBA Name', 'AKA Name', 'Address']]

In [218]:
estab['response_id'] = None
estab['response_alias'] = None
estab['response_name'] =  None
estab['response_latitude'] =  None
estab['response_longitude'] =  None
estab['response_address1'] =  None

#estab = estab.astype({"DBA Name": str, "AKA Name": str, "Address": str, 'response_id': str, 'response_alias': str,\
#                                 "response_name": str, "response_latitude" : float, "response_longitude" : float,\
#                                 "response_address1" : str})

In [219]:
def fill_df(dataframe, responses, try_aka = False):
    """
    Given a dataframe with restaurants
    and Given a list of responses
    Returns the same dataframe with additional columns coming from Yelp
    (condition : If there was 1 match with Yelp)
    And fills up the list of reponses with all responses
    """
    result = dataframe.copy()
    resps = responses.copy()
    for req_nb in range(len(result)):
        PARAM = {#'limit' : 10,
        'name' : result.loc[req_nb]['DBA Name'],
        'address1':result.loc[req_nb]['Address'],
        'city': 'Chicago',
        'state': 'IL',
        'country': 'US'}
        response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
        resps.append(response)
        response_df = json_normalize(response.json()['businesses'])
        #if we get no match for this response, we can try using a different name
        if (try_aka):
            if(len(resps[req_nb].json()['businesses']) == 0):
                PARAM = {#'limit' : 10,
                    'name' : dataframe.loc[req_nb]['AKA_Name'],
                    'address1':dataframe.loc[req_nb]['Address'],
                    'city': 'Chicago',
                    'state': 'IL',
                    'country': 'US'}
                response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
                resps[req_nb] = response
                response_df = json_normalize(response.json()['businesses'])
        #if we get a match, we fill the dataframe 
        if (len(response_df) == 1):
            result['response_id'][req_nb] = response_df['id'][0]
            result['response_alias'][req_nb] = response_df['alias'][0]
            result['response_name'][req_nb] = response_df['name'][0]
            result['response_latitude'][req_nb] = response_df['coordinates.latitude'][0]
            result['response_longitude'][req_nb] = response_df['coordinates.longitude'][0]
            result['response_address1'][req_nb] = response_df['location.address1'][0]
        #resps_df = resps_df.append(json_normalize(response.json()['businesses']), ignore_index=True)
    return result, resps

In [220]:
#don't do requests for the whole dataframe, it's too big
responses = []
dirty_hundred, dirty_resps_hundred = fill_df(estab[0:100], responses)

In [221]:
dirty_hundred.profile_report(style={'full_width':True})

In [232]:
dirty_resps_hundred[0].headers

{'Server': 'nginx', 'Content-Type': 'application/json', 'x-routing-service': '10-65-129-43-useast1bprod; site=public_api_v3', 'ratelimit-remaining': '4690', 'x-b3-sampled': '0', 'x-zipkin-id': 'd7636eb0e0718cbb', 'ratelimit-resettime': '2019-11-24T00:00:00+00:00', 'ratelimit-dailylimit': '5000', 'x-proxied': '10-65-211-19-useast1cprod', 'content-encoding': 'gzip', 'Transfer-Encoding': 'chunked', 'Accept-Ranges': 'bytes', 'Date': 'Sat, 23 Nov 2019 12:59:54 GMT', 'Via': '1.1 varnish', 'Connection': 'keep-alive', 'X-Served-By': 'cache-hhn4076-HHN', 'X-Cache': 'MISS', 'X-Cache-Hits': '0', 'Vary': 'Accept-Encoding'}

### Let's try requests for the first 5000 rows

In [260]:
responses = []

try_aka = False
#I can't the call the function because if an error occurs I can't tell where exactly
#yelp_resp_df_0_4000, yelp_resp_0_5000 = fill_df(estab[0:5000], responses) 
yelp_resp_df_0_5000 = estab[0:5000].copy()
yelp_resp_0_5000 = responses.copy()
for req_nb in range(len(yelp_resp_df_0_5000)):
    if (req_nb%10==0):
        print(f"Request {req_nb} over {len(yelp_resp_df_0_5000)}")
    PARAM = {#'limit' : 10,
        'name' : yelp_resp_df_0_5000.loc[req_nb]['DBA Name'],
        'address1':yelp_resp_df_0_5000.loc[req_nb]['Address'],
        'city': 'Chicago',
        'state': 'IL',
        'country': 'US'}
    response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
    yelp_resp_0_5000.append(response)
    response_df = json_normalize(response.json()['businesses'])
    #if we get no match for this response, we can try using a different name
    if (try_aka):
        if(len(yelp_resp_0_4000[req_nb].json()['businesses']) == 0):
            PARAM = {#'limit' : 10,
                'name' : dataframe.loc[req_nb]['AKA_Name'],
                'address1':dataframe.loc[req_nb]['Address'],
                'city': 'Chicago',
                'state': 'IL',
                'country': 'US'}
            response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
            yelp_resp_0_4000[req_nb] = response
            response_df = json_normalize(response.json()['businesses'])
     #if we get a match, we fill the dataframe 
    if (len(response_df) == 1):
        yelp_resp_df_0_5000['response_id'][req_nb] = response_df['id'][0]
        yelp_resp_df_0_5000['response_alias'][req_nb] = response_df['alias'][0]
        yelp_resp_df_0_5000['response_name'][req_nb] = response_df['name'][0]
        yelp_resp_df_0_5000['response_latitude'][req_nb] = response_df['coordinates.latitude'][0]
        yelp_resp_df_0_5000['response_longitude'][req_nb] = response_df['coordinates.longitude'][0]
        yelp_resp_df_0_5000['response_address1'][req_nb] = response_df['location.address1'][0]           

Request 0 over 5000
Request 5 over 5000
Request 10 over 5000
Request 15 over 5000
Request 20 over 5000
Request 25 over 5000
Request 30 over 5000
Request 35 over 5000
Request 40 over 5000
Request 45 over 5000
Request 50 over 5000
Request 55 over 5000
Request 60 over 5000
Request 65 over 5000
Request 70 over 5000
Request 75 over 5000
Request 80 over 5000
Request 85 over 5000
Request 90 over 5000
Request 95 over 5000
Request 100 over 5000
Request 105 over 5000
Request 110 over 5000
Request 115 over 5000
Request 120 over 5000
Request 125 over 5000
Request 130 over 5000
Request 135 over 5000
Request 140 over 5000
Request 145 over 5000
Request 150 over 5000
Request 155 over 5000
Request 160 over 5000
Request 165 over 5000
Request 170 over 5000
Request 175 over 5000
Request 180 over 5000
Request 185 over 5000
Request 190 over 5000
Request 195 over 5000
Request 200 over 5000
Request 205 over 5000
Request 210 over 5000
Request 215 over 5000
Request 220 over 5000
Request 225 over 5000
Request 23

Request 1830 over 5000
Request 1835 over 5000
Request 1840 over 5000
Request 1845 over 5000
Request 1850 over 5000
Request 1855 over 5000
Request 1860 over 5000
Request 1865 over 5000
Request 1870 over 5000
Request 1875 over 5000
Request 1880 over 5000
Request 1885 over 5000
Request 1890 over 5000
Request 1895 over 5000
Request 1900 over 5000
Request 1905 over 5000
Request 1910 over 5000
Request 1915 over 5000
Request 1920 over 5000
Request 1925 over 5000
Request 1930 over 5000
Request 1935 over 5000
Request 1940 over 5000
Request 1945 over 5000
Request 1950 over 5000
Request 1955 over 5000
Request 1960 over 5000
Request 1965 over 5000
Request 1970 over 5000
Request 1975 over 5000
Request 1980 over 5000
Request 1985 over 5000
Request 1990 over 5000
Request 1995 over 5000
Request 2000 over 5000
Request 2005 over 5000
Request 2010 over 5000
Request 2015 over 5000
Request 2020 over 5000
Request 2025 over 5000
Request 2030 over 5000
Request 2035 over 5000
Request 2040 over 5000
Request 204

Request 3615 over 5000
Request 3620 over 5000
Request 3625 over 5000
Request 3630 over 5000
Request 3635 over 5000
Request 3640 over 5000
Request 3645 over 5000
Request 3650 over 5000
Request 3655 over 5000
Request 3660 over 5000
Request 3665 over 5000
Request 3670 over 5000
Request 3675 over 5000
Request 3680 over 5000
Request 3685 over 5000
Request 3690 over 5000
Request 3695 over 5000
Request 3700 over 5000
Request 3705 over 5000
Request 3710 over 5000
Request 3715 over 5000
Request 3720 over 5000
Request 3725 over 5000
Request 3730 over 5000
Request 3735 over 5000
Request 3740 over 5000
Request 3745 over 5000
Request 3750 over 5000
Request 3755 over 5000
Request 3760 over 5000
Request 3765 over 5000
Request 3770 over 5000
Request 3775 over 5000
Request 3780 over 5000
Request 3785 over 5000
Request 3790 over 5000
Request 3795 over 5000
Request 3800 over 5000
Request 3805 over 5000
Request 3810 over 5000
Request 3815 over 5000
Request 3820 over 5000
Request 3825 over 5000
Request 383

In [262]:
yelp_resp_df_0_5000

DBA Name                         AKA Name  \
0                     YOUNG SCHOLARS ACADEMY           YOUNG SCHOLARS ACADEMY   
1                                OSITO'S TAP                      OSITO'S TAP   
2                           LAS SISTERS INC.                  LAS SISTERS INC   
3     CARNICERIA Y FRUTERIA 'LOS ALTOS' INC.  CARNICERIA Y FRUTERIA LOS ALTOS   
4                     FOODA- 150 N RIVERSIDE            FOODA 150 N RIVERSIDE   
...                                      ...                              ...   
4995                                  CONGAS                           CONGAS   
4996                    EL POLLO GRILL, INC.             EL POLLO GRILL, INC.   
4997                   WRIGLEYVILLE ROOFTOPS            WRIGLEYVILLE ROOFTOPS   
4998                              CHEF XIONG                       CHEF XIONG   
4999                         WESTERN POULTRY                  WESTERN POULTRY   

                         Address             response_id  \
0     10926-10928 S WESTERN AVE                     None   
1           2553 S RIDGEWAY AVE                     None   
2           2700 S TRUMBULL AVE                     None   
3                2959 W 40TH ST   jleGfLhZuxvRUdqAFstVGg   
4           150 N RIVERSIDE PLZ                     None   
...                          ...                     ...   
4995         7021 W HIGGINS AVE   qSrQDsG2BYdCmphu3-qrvA   
4996          2839 S PULASKI RD                     None   
4997       3637 N SHEFFIELD AVE   R4wLWK510K8VpYi_WJzX9g   
4998          2143 S ARCHER AVE   Ydn0Q4uqtokhlHTIwOHeTA   
4999         2003 S WESTERN AVE   rhxhZPLt2y4lVWKT4-8G8w   

                               response_alias  \
0                                        None   
1                                        None   
2                                        None   
3     carniceria-y-fruteria-los-altos-chicago   
4                                        None   
...                                       ...   
4995                           congas-chicago   
4996                                     None   
4997               wrigley-rooftops-chicago-9   
4998     chef-xiong-taste-of-szechuan-chicago   
4999             western-live-poultry-chicago   

                        response_name response_latitude response_longitude  \
0                                None              None               None   
1                                None              None               None   
2                                None              None               None   
3     Carniceria Y Fruteria Los Altos           41.8206           -87.6993   
4                                None              None               None   
...                               ...               ...                ...   
4995                           Congas           41.9802           -87.8033   
4996                             None              None               None   
4997                 Wrigley Rooftops           41.9478            -87.654   
4998   Chef Xiong - Taste of Szechuan           41.8534           -87.6333   
4999             Western Live Poultry           41.8546           -87.6856   

       response_address1  
0                   None  
1                   None  
2                   None  
3         2959 W 40th St  
4                   None  
...                  ...  
4995  7021 W Higgins Ave  
4996                None  
4997    3609 N Sheffield  
4998   2143 S Archer Ave  
4999  2003 S Western Ave  

[5000 rows x 9 columns]

In [263]:
yelp_resp_df_0_5000.profile_report(style={'full_width':True})

In [264]:
yelp_resp_df_0_5000.to_pickle('yelp_match_0_4999')

## BUSINESS MATCH ENDPOINT + CLEAN DATASET: Make requests about establishment from the Chicago food inspections dataset

In [37]:
insp_estab = pd.read_pickle('./datasets/cleaned_inspections.pickle')

In [38]:
insp_estab = insp_estab[['DBA Name', 'AKA Name', 'Address', 'Latitude', 'Longitude']]

In [39]:
insp_estab = insp_estab.drop_duplicates().reset_index(drop = True)
insp_estab

DBA Name  \
0                            YOUNG SCHOLARS ACADEMY   
1             EACH1 TEACH1 LEARNING ACADEMY INC.NFP   
2              EACH 1 TEACH 1 LEARNING ACADEMY INC.   
3                                       OSITO'S TAP   
4                                  LAS SISTERS INC.   
...                                             ...   
31135                                  BK'S BAR-B-Q   
31136  SURF & TURF WHERE SEAFOOD & STEAK MEET, INC.   
31137                       SAFAH FOOD & LIQUOR INC   
31138                                    MAKIA FOOD   
31139                               RAINBOW GROCERY   

                                           AKA Name  \
0                            YOUNG SCHOLARS ACADEMY   
1             EACH1 TEACH1 LEARNING ACADEMY INC.NFP   
2              EACH 1 TEACH 1 LEARNING ACADEMY INC.   
3                                       OSITO'S TAP   
4                                   LAS SISTERS INC   
...                                             ...   
31135                                  BK'S BAR-B-Q   
31136  SURF & TURF WHERE SEAFOOD & STEAK MEET, INC.   
31137                       SAFAH FOOD & LIQUOR INC   
31138                                    MAKIA FOOD   
31139                               RAINBOW GROCERY   

                          Address   Latitude  Longitude  
0      10926-10928 S WESTERN AVE   41.694759 -87.681398  
1      10926-10928 S WESTERN AVE   41.694759 -87.681398  
2         10926-28 S WESTERN AVE   41.694759 -87.681398  
3            2553 S RIDGEWAY AVE   41.844597 -87.718313  
4            2700 S TRUMBULL AVE   41.842512 -87.711225  
...                           ...        ...        ...  
31135             2152 E 71ST ST   41.766393 -87.571724  
31136       13205 S MUSKEGON AVE   41.655351 -87.554280  
31137          7105 S RACINE AVE   41.764896 -87.653965  
31138      2458 S CALIFORNIA AVE   41.846516 -87.695423  
31139             2003 W 69TH ST   41.768328 -87.673819  

[31140 rows x 5 columns]

In [40]:
insp_estab.head(5)

DBA Name  \
0                 YOUNG SCHOLARS ACADEMY   
1  EACH1 TEACH1 LEARNING ACADEMY INC.NFP   
2   EACH 1 TEACH 1 LEARNING ACADEMY INC.   
3                            OSITO'S TAP   
4                       LAS SISTERS INC.   

                                AKA Name                     Address  \
0                 YOUNG SCHOLARS ACADEMY  10926-10928 S WESTERN AVE    
1  EACH1 TEACH1 LEARNING ACADEMY INC.NFP  10926-10928 S WESTERN AVE    
2   EACH 1 TEACH 1 LEARNING ACADEMY INC.     10926-28 S WESTERN AVE    
3                            OSITO'S TAP        2553 S RIDGEWAY AVE    
4                        LAS SISTERS INC        2700 S TRUMBULL AVE    

    Latitude  Longitude  
0  41.694759 -87.681398  
1  41.694759 -87.681398  
2  41.694759 -87.681398  
3  41.844597 -87.718313  
4  41.842512 -87.711225

In [41]:
ENDPOINT = 'https://api.yelp.com/v3/businesses/search'

In [42]:
insp_estab['response_id'] = None
insp_estab['response_alias'] = None
insp_estab['response_name'] =  None
insp_estab['response_latitude'] =  None
insp_estab['response_longitude'] =  None
insp_estab['response_address1'] =  None
insp_estab['response_address2'] =  None
insp_estab['response_address3'] =  None
insp_estab['response_zip_code'] =  None
insp_estab = insp_estab.astype({"DBA Name": str, "AKA Name": str, "Address": str, "Latitude": float,\
                                  "Longitude": float, 'response_id': str, 'response_alias': str,\
                                 "response_name": str, "response_latitude" : float, "response_longitude" : float,\
                                 "response_address1" : str, "response_address2" : str, "response_address3" : str,\
                                 "response_zip_code" : float})

In [67]:
def fill_df(dataframe, responses):
    """
    Given a dataframe with restaurants
    and Given a list of responses
    Returns the same dataframe with additional columns coming from Yelp
    (condition : If there was 1 match with Yelp)
    And fills up the list of reponses with all responses
    """
    result = dataframe.copy()
    resps = responses.copy()
    for req_nb in range(len(dataframe)):
        PARAM = {#'limit' : 10,
            'name' : dataframe.loc[req_nb]['DBA Name'],
            'address1':dataframe.loc[req_nb]['Address'],
            'city': 'Chicago',
            'state': 'IL',
            'country': 'US'}
        response = requests.get(url=ENDPOINT, params=PARAM, headers = HEADERS)
        resps.append(response)
        response_df = json_normalize(response.json()['businesses'])
        if (len(response_df) == 1):
            result['response_id'][req_nb] = response_df['id'][0]
            result['response_alias'][req_nb] = response_df['alias'][0]
            result['response_name'][req_nb] = response_df['name'][0]
            result['response_latitude'][req_nb] = response_df['coordinates.latitude'][0]
            result['response_longitude'][req_nb] = response_df['coordinates.longitude'][0]
            result['response_address1'][req_nb] = response_df['location.address1'][0]
            result['response_address2'][req_nb] = response_df['location.address2'][0]
            result['response_address3'][req_nb] = response_df['location.address3'][0]
            result['response_zip_code'][req_nb] = response_df['location.zip_code'][0]
        #resps_df = resps_df.append(json_normalize(response.json()['businesses']), ignore_index=True)
    return result, resps

In [68]:
#don't do requests for the whole dataframe, it's too big
responses = []
requests_hundred, resps_hundred = fill_df(insp_estab[0:100], responses)

In [91]:
requests_hundred.head(20)

DBA_Name  \
0                   YOUNG SCHOLARS ACADEMY   
1    EACH1 TEACH1 LEARNING ACADEMY INC.NFP   
2     EACH 1 TEACH 1 LEARNING ACADEMY INC.   
3                              OSITO'S TAP   
4                         LAS SISTERS INC.   
5                    SAORY RESTAURANT, INC   
6                        TAQUERIA MARTINEZ   
7                    DELISIAS MEXICANAS #2   
8                      LOS SAUCES TAQUERIA   
9   CARNICERIA Y FRUTERIA 'LOS ALTOS' INC.   
10                           CLUB CLUBMONO   
11                  FOODA- 150 N RIVERSIDE   
12                   BROWN BAG SEAFOOD CO.   
13                          11 DINING, LLC   
14                 PORTER KITCHEN AND DECK   
15                            SMALL CHEVAL   
16                                   HYATT   
17                        GATEWAY NEWSTAND   
18                 STARBUCKS COFFEE #47565   
19          CHICAGO'S FINEST BEEF AND BREW   

                                     AKA_Name                     Address  \
0                      YOUNG SCHOLARS ACADEMY  10926-10928 S WESTERN AVE    
1       EACH1 TEACH1 LEARNING ACADEMY INC.NFP  10926-10928 S WESTERN AVE    
2        EACH 1 TEACH 1 LEARNING ACADEMY INC.     10926-28 S WESTERN AVE    
3                                 OSITO'S TAP        2553 S RIDGEWAY AVE    
4                             LAS SISTERS INC        2700 S TRUMBULL AVE    
5                       SAORY RESTAURANT, INC        2700 S TRUMBULL AVE    
6                           TAQUERIA MARTINEZ        2700 S TRUMBULL AVE    
7                       DELISIAS MEXICANAS #2        2700 S TRUMBULL AVE    
8                         LOS SAUCES TAQUERIA        2700 S TRUMBULL AVE    
9             CARNICERIA Y FRUTERIA LOS ALTOS             2959 W 40TH ST    
10                              CLUB CLUBMONO             2959 W 40TH ST    
11                      FOODA 150 N RIVERSIDE        150 N RIVERSIDE PLZ    
12                      BROWN BAG SEAFOOD CO.        150 N RIVERSIDE PLZ    
13                                  11 DINING        150 N RIVERSIDE PLZ    
14                    PORTER KITCHEN AND DECK        150 N RIVERSIDE PLZ    
15                               SMALL CHEVAL        150 N RIVERSIDE PLZ    
16                                 HUB 8 CAFE        150 N RIVERSIDE PLZ    
17  GATEWAY NEWSTAND/150 N RIVERSIDE BUILDING        150 N RIVERSIDE PLZ    
18                                 STARBUCK'S        150 N RIVERSIDE PLZ    
19             CHICAGO'S FINEST BEEF AND BREW           234 S WABASH AVE    

     Latitude  Longitude             response_id  \
0   41.694759 -87.681398                    None   
1   41.694759 -87.681398                    None   
2   41.694759 -87.681398                    None   
3   41.844597 -87.718313                    None   
4   41.842512 -87.711225                    None   
5   41.842512 -87.711225                    None   
6   41.842512 -87.711225                    None   
7   41.842512 -87.711225                    None   
8   41.842512 -87.711225  IM5F-cWwmWRtcclsRUD_2w   
9   41.820772 -87.699407  jleGfLhZuxvRUdqAFstVGg   
10  41.820772 -87.699407                    None   
11  41.885089 -87.638406                    None   
12  41.885089 -87.638406  PKG7oZgjMmrpcK0Fy3UIJg   
13  41.885089 -87.638406                    None   
14  41.885089 -87.638406  OHl34eI8EENNANB0fuQA4w   
15  41.885089 -87.638406  dNp99d8nWWuxmSR0ZLyJxQ   
16  41.885089 -87.638406                    None   
17  41.885089 -87.638406                    None   
18  41.885089 -87.638406  cXb0illXLBQlZBrh6hFmfw   
19  41.878674 -87.626242  KwnuxV_YLkHUfP3dhe_qZg   

                             response_alias                    response_name  \
0                                      None                             None   
1                                      None                             None   
2                                      None                             None   
3                                   

In [264]:
x = [(resp.json()) for resp in resps_hundred]

In [265]:
[len(a['businesses'])>=1 for a in x]

[False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 True,
 True,
 False,
 False,
 True,
 False,
 True,
 True,
 False,
 False,
 False,
 True,
 True,
 True,
 False,
 False,
 False,
 False,
 False,
 False,
 True,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 True,
 False,
 True,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 True,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 True,
 True,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False,
 False]

In [69]:
requests_hundred.profile_report(style={'full_width':True})